In [1]:
!pip install pytimetk

!pip install feature-engine --no-deps
!pip install model-diagnostics
# !pip install glum
!pip install skimpy
!pip install optuna
!pip install skforecast
!pip install shap
!pip install ydata_profiling
!pip install missingno
!pip install statsforecast
# !pip install pmdarima
!pip install category-encoders

!pip install kaggle

!pip install xgboost
!pip install lightgbm
!pip install shap

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 233.8/233.8 kB 6.8 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.3/4.3 MB 55.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 991.0/991.0 kB 37.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 82.3/82.3 kB 5.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 42.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 36.3/36.3 MB 38.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.8/10.8 MB 86.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 59.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 985.3/985.3 kB 46.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 119.7/119.7 kB 9.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 kB 9.4 MB/s eta 0:0

In [2]:
!mkdir -p ~/.kaggle
!cp kaggle.json ~/.kaggle/
!chmod 600 ~/.kaggle/kaggle.json

In [3]:
!kaggle competitions download -c store-sales-time-series-forecasting

!unzip -q store-sales-time-series-forecasting.zip

  0% 0.00/21.4M [00:00<?, ?B/s]
100% 21.4M/21.4M [00:00<00:00, 1.11GB/s]


# 🔮 Kaggle Challenge: Predicción de Ventas por Tienda 🛒  
## 🏆 SMAPE: **0.43318** — ¡Top 10% en la competencia oficial!

---
## 🎯 Objetivo de la Competencia

En esta competencia de Kaggle, el objetivo es construir un modelo de series temporales para **predecir las ventas unitarias de miles de productos** vendidos en diversas tiendas de *Corporación Favorita*, un importante minorista de comestibles con sede en Ecuador.

Los participantes deben generar pronósticos diarios por tienda y categoría de producto, utilizando variables como fechas, promociones, feriados, y atributos del producto.
### 🧠 Estrategia General

Este notebook implementa un enfoque de predicción de ventas en múltiples etapas:

1. 📊 **Análisis exploratorio** de estacionalidad y lags
2. 🛠️ **Ingeniería de características**: Fourier, fechas, promociones (vía pipeline)
3. 🚫 Primer modelo **sin lags** (no autoregresivo) para entender la importancia de features
4. 🔁 Modelo **autoregresivo** usando lags seleccionados
5. 🚀 Propuestas de mejoras: stacking, nuevas features

In [4]:
# Core y manejo de datos
import numpy as np
import pandas as pd
import re
import time
import warnings

# Visualización
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Configuración de estilo para matplotlib
plt.style.use('fivethirtyeight')
plt.rcParams['lines.linewidth'] = 1.5
plt.rcParams['font.size'] = 10

# Exploración y limpieza
from skimpy import skim, clean_columns
from ydata_profiling import ProfileReport
import missingno as msno

# Manejo de fechas y feriados
from holidays import Ecuador as HolCal
import pytimetk as tk

# Machine Learning - Scikit-Learn
from sklearn.model_selection import (
    train_test_split, GridSearchCV, RandomizedSearchCV,
    StratifiedKFold, cross_val_score
)
from sklearn.pipeline import Pipeline
from sklearn.metrics import (
    mean_squared_error, mean_absolute_error, r2_score,
    confusion_matrix, classification_report,
    precision_score, recall_score, f1_score,
    accuracy_score, balanced_accuracy_score,
    average_precision_score, roc_auc_score
)
from sklearn.preprocessing import (
    StandardScaler, MinMaxScaler, RobustScaler,
    OneHotEncoder, LabelEncoder, KBinsDiscretizer,
    Binarizer
)
from sklearn.linear_model import Ridge, LogisticRegression
from sklearn.svm import SVC
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import (
    RandomForestRegressor, RandomForestClassifier,
    ExtraTreesClassifier
)

# XGBoost y LightGBM
from xgboost import XGBClassifier, XGBRegressor
import lightgbm as lgb

# SHAP y Optuna
import shap
import optuna

# Feature engineering con Feature-engine
from feature_engine.imputation import (
    AddMissingIndicator, MeanMedianImputer, CategoricalImputer
)
from feature_engine.outliers import Winsorizer
from feature_engine.selection import (
    DropDuplicateFeatures, DropConstantFeatures, DropFeatures
)
from feature_engine.discretisation import (
    EqualFrequencyDiscretiser, EqualWidthDiscretiser
)
from feature_engine.encoding import (
    OneHotEncoder as OneHotEncoder_f, RareLabelEncoder, OrdinalEncoder
)
from feature_engine.transformation import (
    LogTransformer, YeoJohnsonTransformer
)
from feature_engine.wrappers import SklearnTransformerWrapper
from feature_engine.timeseries.forecasting import (
    LagFeatures, WindowFeatures, ExpandingWindowFeatures
)

# Skforecast
from skforecast.datasets import fetch_dataset
from skforecast.recursive import ForecasterRecursive
from skforecast.direct import ForecasterDirect
from skforecast.model_selection import (
    TimeSeriesFold, grid_search_forecaster, backtesting_forecaster
)
from skforecast.preprocessing import RollingFeatures
from skforecast.utils import save_forecaster, load_forecaster
from skforecast.metrics import calculate_coverage
from skforecast.plot import plot_prediction_intervals

# Statsmodels para autocorrelaciones y suavizado
from statsmodels.tsa.stattools import acf, pacf
from statsmodels.nonparametric.smoothers_lowess import lowess

# Otros
import category_encoders as ce
from sklearn import set_config
set_config(transform_output="pandas")
warnings.filterwarnings('once')


In [5]:
def categ_vari(X_train,date_var=["date"]):
  cat_vars=[xx for xx in X_train.columns if X_train[xx].dtype =="O" ]

  num_vars=[xx for xx in X_train.columns if X_train[xx].dtype !="O" and xx not in date_var]


  discrete_vars=[ xx for xx in num_vars if len(X_train[xx].unique())<=30]

  cont_vars=[ xx for xx in num_vars if xx not in discrete_vars]
  var_all=cat_vars+num_vars

  return cat_vars,num_vars,discrete_vars,cont_vars,var_all

def add_time_features(df, date_col='date', periods=[1,2,6,7,13,14], max_order=2, engine="pandas"):
    df_dates = df[[date_col]].drop_duplicates()
    df_dates = df_dates.augment_fourier(
        date_column=date_col,
        periods=periods,
        max_order=max_order,
        engine=engine
    )
    df_dates = df_dates.augment_timeseries_signature(date_col)
    return df.merge(df_dates, on=date_col, how='left')


## 📦 Descripción del Dataset

En esta competencia se busca predecir las ventas diarias por categoría de producto en diferentes tiendas de la cadena **Corporación Favorita** en Ecuador. Para ello, se dispone de una rica colección de fuentes de datos que capturan aspectos temporales, promocionales, económicos y geográficos.

### 📁 Archivos y Campos Principales

- **`train.csv`**  
  Contiene las series temporales históricas con las siguientes columnas:
  - `date`: Fecha de la observación  
  - `store_nbr`: Identificador de tienda  
  - `family`: Categoría de producto  
  - `sales`: Ventas diarias (puede incluir valores fraccionales, ej: 1.5 kg)  
  - `onpromotion`: Número de ítems en promoción ese día en la tienda

- **`test.csv`**  
  Mismo formato que `train.csv`, pero sin la columna `sales`. Contiene 15 días posteriores al último dato del entrenamiento.

- **`sample_submission.csv`**  
  Archivo de ejemplo con el formato esperado para la predicción.

- **`stores.csv`**  
  Metadatos de las tiendas:
  - `city`, `state`, `type`, `cluster` (agrupaciones de tiendas similares)

- **`oil.csv`**  
  Precio diario del petróleo — importante ya que Ecuador es un país económicamente sensible a su precio.

- **`holidays_events.csv`**  
  Detalles de días festivos y eventos relevantes:
  - Incluye columnas como `type`, `locale`, `description`, `transferred`  
  - ⚠️ Atención a feriados transferidos, días puente (`Bridge`) y días laborables extraordinarios (`Work Day`) que afectan el comportamiento de consumo.

### 📝 Notas Adicionales Relevantes

- 🧾 **Pagos quincenales** en el sector público (días 15 y último del mes) podrían alterar patrones de compra.
- 🌍 Un terremoto de **magnitud 7.8** ocurrió el 16 de abril de 2016, afectando significativamente las ventas durante semanas, especialmente productos esenciales como agua o alimentos básicos.

---

In [6]:
train_df = pd.read_csv('train.csv',parse_dates=["date"])
test_df = pd.read_csv('test.csv',parse_dates=["date"])

oil=pd.read_csv('oil.csv',parse_dates=["date"])
holy= pd.read_csv('holidays_events.csv',parse_dates=["date"])
stores= pd.read_csv('stores.csv')

<frozen importlib._bootstrap>:1047: ImportWarning: _PyDriveImportHook.find_spec() not found; falling back to find_module()
<frozen importlib._bootstrap>:1047: ImportWarning: _BokehImportHook.find_spec() not found; falling back to find_module()


## 🔍 Exploración de Lags y Estacionalidad

Antes de construir cualquier modelo de series temporales, es fundamental entender **la estructura temporal** de la variable objetivo (`sales`). En particular, buscamos responder:

- ¿Cuánto influye el pasado reciente en las ventas futuras?
- ¿Existen patrones **estacionales recurrentes** en las ventas?
- ¿Cuáles son los lags más **informativos** y consistentes entre diferentes series?

### 🎯 ¿Qué hacemos en este análisis?

1. Creamos múltiples **valores rezagados (lags)** de las ventas.
2. Calculamos la **correlación** entre esos lags y las ventas reales, por cada combinación `store_nbr` × `family`.
3. Graficamos un **boxplot** de las correlaciones absolutas para cada lag.

### 📈 ¿Por qué es útil este gráfico?

Este análisis cumple **doble propósito**:

#### 1. Evaluación de Lags Predictivos
- Identificamos los **lags que más aportan señal predictiva**.
- Detectamos cuáles lags muestran **consistencia** en su correlación positiva o negativa con la variable objetivo.

#### 2. Análisis de Estacionalidad
- Si ciertos lags (por ejemplo, 7, 14, 30) muestran alta correlación, eso sugiere la presencia de **patrones semanales o mensuales recurrentes**.
- Es una forma empírica y visual de **detectar estacionalidad** incluso si no está explícitamente modelada.

### 📦 ¿Por qué usar boxplots?

Los boxplots permiten:
- Ver la **distribución de la fuerza de la relación** entre cada lag y la variable objetivo.
- Comparar fácilmente la **variabilidad entre series temporales**.
- Usar una **línea de corte** basada en la regla del IQR (1.5 × rango intercuartílico) para identificar **lags outliers altamente informativos**.

> 🧠 Este enfoque es modular y escalable: se puede aplicar a cualquier métrica y a múltiples identificadores temporales.


In [7]:


def analyze_lag_correlation(
    df,
    date_col: str,
    target_col: str,
    group_cols: list,
    lag_range: tuple = (1, 30),
    top_k: int = None
):
    """
    Analiza autocorrelación de lags por grupo.

    Args:
        df (pd.DataFrame): Dataset original.
        date_col (str): Columna de fecha.
        target_col (str): Variable objetivo.
        group_cols (list): Columnas para agrupar la serie temporal.
        lag_range (tuple): Rango de lags (start, end).
        top_k (int): Mostrar solo los top_k lags más relevantes (por media de correlación).
    """
    t0 = time.time()

    # ------------------------- Paso 1: Crear lags -------------------------
    aux = df.groupby(group_cols).augment_lags(
        date_column=date_col,
        value_column=target_col,
        lags=lag_range
    )

    aux.columns = [
        col.replace(f"{target_col}_lag_", "lag_") if col.startswith(f"{target_col}_lag_") else col
        for col in aux.columns
    ]

    # ------------------------- Paso 2: Melt largo-forma -------------------------
    aux_melt = aux.melt(
        id_vars=[*group_cols, date_col, target_col],
        value_vars=[col for col in aux.columns if col.startswith("lag_")],
        var_name="variable",
        value_name="value"
    )

    # ------------------------- Paso 3: Correlaciones -------------------------
    corre_df = (
        aux_melt.groupby(group_cols + ["variable"])
        .apply(lambda d: d[target_col].corr(d["value"]))
        .reset_index(name="corre")
    )

    aux_merged = aux_melt.merge(corre_df, on=group_cols + ["variable"], how="left")

    # ------------------------- Paso 4: Valores absolutos -------------------------
    corr_abs = aux_merged[["variable", "corre"]].drop_duplicates().copy()
    corr_abs["corre"] = corr_abs["corre"].abs()

    # ------------------------- Paso 5: Corte de outliers -------------------------
    brk = (corr_abs["corre"].quantile(0.75) - corr_abs["corre"].quantile(0.25)) * 1.5

    # ------------------------- Paso 6: Orden por importancia -------------------------
    corr_order = corr_abs.groupby("variable")["corre"].mean().reset_index().sort_values("corre", ascending=False)
    lag_list = corr_order.variable.head(top_k).tolist() if top_k else corr_order.variable.tolist()

    # ------------------------- Paso 7: Gráfico -------------------------
    fig = go.Figure()
    for lag in lag_list:
        df_lag = corr_abs[corr_abs["variable"] == lag]
        fig.add_trace(go.Box(
            y=df_lag["corre"],
            name=lag,
            marker_color="blue",
            boxpoints="outliers"
        ))

    fig.add_hline(y=brk, line_color="red")
    fig.add_annotation(
        x=len(lag_list) - 1,
        y=brk + 0.03,
        text=f"Outlier Break Point = {brk:.3f}",
        showarrow=False,
        font=dict(color="red")
    )


    fig.update_layout(
    title="📉 Correlaciones Absolutas con Lags",
    yaxis=dict(range=[0, 1], title="|Correlación|"),
    xaxis=dict(tickangle=90, title="Lags"),
    height=600,  # Ajusta la altura para que no se corte en Colab
    width=1000,  # Ancho generoso para mostrar bien los lags
    margin=dict(t=80, b=100)
)
    fig.show()

    print(f"✅ Análisis completado en {time.time() - t0:.2f} segundos.")



analyze_lag_correlation(
    df=train_df,
    date_col="date",
    target_col="sales",
    group_cols=["store_nbr", "family"],
    lag_range=(1, 30),
    top_k=20  # Opcional, top 20 lags más importantes
)

<frozen importlib._bootstrap>:1047: ImportWarning: _PyDriveImportHook.find_spec() not found; falling back to find_module()
<frozen importlib._bootstrap>:1047: ImportWarning: _BokehImportHook.find_spec() not found; falling back to find_module()
<frozen importlib._bootstrap>:1047: ImportWarning: _PyDriveImportHook.find_spec() not found; falling back to find_module()
<frozen importlib._bootstrap>:1047: ImportWarning: _BokehImportHook.find_spec() not found; falling back to find_module()
<frozen importlib._bootstrap>:1047: ImportWarning:

_PyDriveImportHook.find_spec() not found; falling back to find_module()

<frozen importlib._bootstrap>:1047: ImportWarning:

_BokehImportHook.find_spec() not found; falling back to find_module()



✅ Análisis completado en 101.34 segundos.


In [8]:


def plot_time_series_seasonality(
    data,
    time_col="timestamp",
    y_col="users",
    group_cols=None,
    top_groups=20,
    seasonality_vars=None
):
    df = data.copy().reset_index(drop=True)
    df[time_col] = pd.to_datetime(df[time_col])

    if seasonality_vars is None:
        seasonality_vars = ["month", "week_day", "hour_day", "day_hour"]

    if "month" in seasonality_vars:
        df["month"] = df[time_col].dt.month
    if "week_day" in seasonality_vars:
        df["week_day"] = df[time_col].dt.dayofweek + 1
    if "hour_day" in seasonality_vars:
        df["hour_day"] = df[time_col].dt.hour + 1
    if "day_hour" in seasonality_vars:
        if "week_day" not in df.columns:
            df["week_day"] = df[time_col].dt.dayofweek + 1
        if "hour_day" not in df.columns:
            df["hour_day"] = df[time_col].dt.hour + 1
        df["day_hour"] = (df["week_day"] - 1) * 24 + df["hour_day"]
    if "week_of_year" in seasonality_vars:
        df["week_of_year"] = df[time_col].dt.isocalendar().week
    if "day_of_month_bin" in seasonality_vars:
        bins = [0, 7, 14, 21, 31]
        labels = ['Week1', 'Week2', 'Week3', 'Week4']
        df["day_of_month_bin"] = pd.cut(df[time_col].dt.day, bins=bins, labels=labels, right=True)

    # Selección correcta de top grupos
    if group_cols:
        top_group_values = (
            df.groupby(group_cols)[y_col].sum()
            .sort_values(ascending=False)
            .head(top_groups)
            .reset_index()
        )
        df = df.merge(top_group_values[group_cols], on=group_cols, how="inner")

    plots = []

    def create_box_and_line(df_grouped, x, title, xlabel):
        fig = go.Figure()
        fig.add_trace(go.Box(
            y=df_grouped[y_col],
            x=df_grouped[x],
            name="Distribution",
            boxpoints='outliers',
            marker=dict(opacity=0.5)
        ))
        medians = df_grouped.groupby(x)[y_col].median().reset_index()
        fig.add_trace(go.Scatter(
            x=medians[x],
            y=medians[y_col],
            mode="lines+markers",
            name="Median",
            line=dict(color="black")
        ))
        fig.update_layout(title=title, xaxis_title=xlabel, yaxis_title=y_col)
        return fig

    for var in seasonality_vars:
        if var in df.columns:
            xlabel = var.replace("_", " ").title()
            title = f"{y_col} distribution by {xlabel}"
            plots.append(create_box_and_line(df, var, title, xlabel))

    return plots

plots = plot_time_series_seasonality(
    data=train_df,
    time_col="date",
    y_col="sales",
    group_cols=["store_nbr", "family"],
    top_groups=10,
    seasonality_vars=["month", "week_day", "week_of_year", "day_of_month_bin"]
)

for fig in plots:
    fig.show()

<frozen importlib._bootstrap>:1047: ImportWarning:

_PyDriveImportHook.find_spec() not found; falling back to find_module()

<frozen importlib._bootstrap>:1047: ImportWarning:

_BokehImportHook.find_spec() not found; falling back to find_module()

<frozen importlib._bootstrap>:1047: ImportWarning:

_PyDriveImportHook.find_spec() not found; falling back to find_module()

<frozen importlib._bootstrap>:1047: ImportWarning:

_BokehImportHook.find_spec() not found; falling back to find_module()



In [12]:
# Calcular ventas por grupo y seleccionar los 40 más importantes
# Uso pytimetk para dibujar con scroll cada una de estas series por separado
top_40 = (
    train_df
    .groupby(["store_nbr", "family"], as_index=False)["sales"]
    .sum()
    .assign(
        sales_pct=lambda df: df["sales"] / df["sales"].sum()
    )
    .sort_values("sales_pct", ascending=False)
    .head(40)
)[["store_nbr", "family"]]
top_40=top_40.merge(train_df,on=["store_nbr", "family"],how="left")
top_40


top_40.groupby(["store_nbr", "family"])\
 .plot_timeseries(
        date_column = 'date',
        value_column = 'sales',
        title = 'Ventas por dia por tienda y familia',
        facet_ncol = 3,
        facet_scales = "free",
        y_intercept_color = tk.palette_timetk()['steel_blue'],
        width = 1000,
        height = 800,
        y_lab = 'Total Sales',
        plotly_dropdown=True,
        plotly_dropdown_x=0,
        plotly_dropdown_y=1,
        engine = 'plotly'
    )

<frozen importlib._bootstrap>:1047: ImportWarning:

_PyDriveImportHook.find_spec() not found; falling back to find_module()

<frozen importlib._bootstrap>:1047: ImportWarning:

_BokehImportHook.find_spec() not found; falling back to find_module()

<frozen importlib._bootstrap>:1047: ImportWarning:

_PyDriveImportHook.find_spec() not found; falling back to find_module()

<frozen importlib._bootstrap>:1047: ImportWarning:

_BokehImportHook.find_spec() not found; falling back to find_module()



In [13]:

# Definir número máximo de lags a calcular
## analisis de ACF y PACF por grupo store_nbr y family
max_lags = 40


# Listas para almacenar resultados
acf_results = []
pacf_results = []

# Iterar sobre cada grupo
# Iterar sobre cada grupo
for (s,f), group_df in top_40.groupby(["store_nbr","family"]):
    series = group_df.sort_values("date")["sales"].values

    # Calcular ACF y PACF
    acf_vals = acf(series, nlags=max_lags, fft=False, missing='drop')
    pacf_vals = pacf(series, nlags=max_lags, method='ywmle')

    # Guardar resultados en listas
    # acf_results.append(((int(s),f), acf_vals))
    # pacf_results.append(((int(s),f), pacf_vals))
    acf_results.append(( str(int(s))+"_"+str(f), acf_vals,len(series)))
    pacf_results.append((str(int(s))+"_"+str(f), pacf_vals,len(series)))

def plot_acf_pacf_stem(results, title="ACF"):
    fig = go.Figure()
    trace_count = 0
    cutups = []

    for i, (unique_id, values, n_obs) in enumerate(results):
        values = values[1:]                  # Excluir lag 0
        lags = np.arange(1, len(values) + 1)
        cut_up = 2 / np.sqrt(n_obs)
        cutups.append(cut_up)

        # Líneas verticales (stems)
        for lag, val in zip(lags, values):
            fig.add_trace(
                go.Scatter(
                    x=[lag, lag],
                    y=[0, val],
                    mode='lines',
                    line=dict(color='blue'),
                    showlegend=False,
                    visible=(i == 0)
                )
            )
            trace_count += 1

        # Puntos (tops)
        fig.add_trace(
            go.Scatter(
                x=lags,
                y=values,
                mode='markers',
                marker=dict(color='blue', size=6),
                name=unique_id,
                showlegend=False,
                visible=(i == 0)
            )
        )
        trace_count += 1

        # Líneas horizontales de corte
        for y_val in [cut_up, -cut_up]:
            fig.add_trace(
                go.Scatter(
                    x=[lags[0], lags[-1]],
                    y=[y_val, y_val],
                    mode='lines',
                    line=dict(color='red', dash='dash'),
                    showlegend=False,
                    visible=(i == 0)
                )
            )
            trace_count += 1

        # Anotación de valor de corte
        fig.add_annotation(
            x=lags[-1], y=cut_up,
            text=f"cut-up ≈ {cut_up:.3f}",
            showarrow=False,
            font=dict(color='red'),
            yanchor="bottom",
            visible=(i == 0),
            name=f"cutup-label-{i}"
        )

    # Dropdown buttons
    buttons = []
    trace_idx = 0
    for i, (unique_id, values, n_obs) in enumerate(results):
        n_stems = len(values[1:])
        total_traces = n_stems + 1 + 2  # stems + markers + 2 hlines
        visibility = [False] * trace_count

        for j in range(total_traces):
            visibility[trace_idx + j] = True
        trace_idx += total_traces

        # Anotaciones también son visibles por grupo
        annotations = []
        for j in range(len(results)):
            annotations.append(dict(visible=(j == i)))

        buttons.append(dict(
            label=unique_id,
            method="update",
            args=[
                {"visible": visibility},
                {"title": f"{title}: {unique_id}", "annotations": annotations}
            ]
        ))

    # Inicial layout
    fig.update_layout(
        updatemenus=[
            dict(
                buttons=buttons,
                direction="down",
                showactive=True,
                x=0,
                y=1.15,
            )
        ],
        title=f"{title}: {results[0][0]}",
        xaxis_title="Lag",
        yaxis_title="Correlation",
        height=500
    )

    return fig




fig_acf = plot_acf_pacf_stem(acf_results, title="ACF")
fig_pacf = plot_acf_pacf_stem(pacf_results, title="PACF")

fig_acf.show()
fig_pacf.show()

<frozen importlib._bootstrap>:1047: ImportWarning:

_PyDriveImportHook.find_spec() not found; falling back to find_module()

<frozen importlib._bootstrap>:1047: ImportWarning:

_BokehImportHook.find_spec() not found; falling back to find_module()



## 🔁 Análisis de Lags y Estacionalidad

Como parte del análisis exploratorio, se estudió la **autocorrelación** de las ventas para detectar patrones temporales repetitivos y determinar rezagos informativos relevantes.

---

### 📈 Observaciones clave

- Las ventas presentan **fuerte autocorrelación a corto y medio plazo**.
- Se identificaron **picos de correlación significativa** en los siguientes rezagos:
  - 📌 **Lag 1 y 2**: Capturan la inercia inmediata del comportamiento de compra.
  - 📆 **Lag 6 y 7**: Reflejan patrones semanales (mismo día de la semana anterior).
  - 🔄 **Lag 13 y 14**: Indican efectos quincenales (dos ciclos semanales).

---

### 🧮 Ventanas de Promedios Móviles (Rolling)

- Se evaluaron distintas ventanas para promedios móviles de ventas.
- La **ventana de 14 días** resultó ser la más informativa, ya que combina:
  - Tendencia reciente (últimas dos semanas)
  - Variación estacional semanal y quincenal

---

### ✅ Conclusiones y variables seleccionadas

Basado en este análisis, se utilizarán las siguientes variables:

- **Lags incluidos** como features:
  - `lag_1`, `lag_2`, `lag_6`, `lag_7`, `lag_13`, `lag_14`

- **Ventanas móviles (rolling) sobre ventas**:
  - `rolling_mean_14`: media móvil
  - `rolling_std_14`: desviación estándar (variabilidad)
  - `rolling_max_14`: valor máximo reciente (comportamiento extremo)

---

> 📌 Estas variables ayudan al modelo a capturar tanto patrones inmediatos como estacionales, y proporcionan contexto adicional sobre la estabilidad o variabilidad de las ventas recientes.


In [14]:
## El precio de petróleo debemos imputar los valores faltantes
oil2=oil.copy()

oil2["imputed_value"] =oil2["dcoilwtico"].fillna(method="ffill")

oil2["imputed_value"] =oil2["imputed_value"].fillna(method="bfill")

#oil2["imputed_value"] =oil2["imputed_value"].interpolate()
# Identificamos las posiciones donde el valor fue imputado
oil2["was_imputed"] = oil2["dcoilwtico"].isnull()

# Creamos el gráfico
fig = go.Figure()

# Serie original (incluye valores imputados)
fig.add_trace(go.Scatter(
    x=oil2["date"],
    y=oil2["imputed_value"],
    mode="lines+markers",
    name="Serie (con imputación)",
    line=dict(color="blue"),
    marker=dict(size=6)
))

# Solo los puntos imputados
fig.add_trace(go.Scatter(
    x=oil2[oil2["was_imputed"]]["date"],
    y=oil2[oil2["was_imputed"]]["imputed_value"],
    mode="markers",
    name="Valores imputados",
    marker=dict(color="red", size=8, symbol="circle"),
    showlegend=True
))

fig.update_layout(
    title="Serie temporal con imputación de valores nulos",
    xaxis_title="Fecha",
    yaxis_title="Valor",
    template="plotly_white"
)

fig.show()

<frozen importlib._bootstrap>:1047: ImportWarning:

_PyDriveImportHook.find_spec() not found; falling back to find_module()

<frozen importlib._bootstrap>:1047: ImportWarning:

_BokehImportHook.find_spec() not found; falling back to find_module()



## 📅 Enriquecimiento de Fechas, Feriados y Contexto Económico

Además de las variables temporales básicas provistas en el dataset original, se realizó una ampliación significativa del conjunto de características relacionadas con el tiempo, la estacionalidad y el contexto económico.

---

## 🛢️ Imputación del Precio del Petróleo e Interacciones

El dataset incluía valores del precio del petróleo (`oil_price`), una variable exógena relevante para analizar el impacto económico general en el comportamiento de compra.

### 🔧 Imputación de Valores Faltantes

- Se detectaron valores faltantes en la serie temporal del precio del petróleo, respecto a la frecuencia original de la serie de tiempo.
- Para mantener la coherencia temporal, se aplicó una **imputación forward-fill (`ffill`)**, propagando el último valor conocido hacia adelante.
- Este método preserva la dinámica realista de la serie sin introducir fugas de información futura.

### 🧠 Interacciones Derivadas

Para capturar relaciones no lineales o efectos contextuales, se generaron las siguientes **interacciones cruzadas**:

- 📊 `oil_price × promo`:  
  Modela cómo varía la respuesta a promociones en función de fluctuaciones económicas.

- 🎛️ `oil_price × componentes de Fourier`:  
  Permite capturar modulaciones estacionales en el impacto del petróleo sobre las ventas.  
  Por ejemplo, el efecto de un precio elevado del petróleo puede amplificarse en ciertos meses o estaciones del año.

---

## 🎉 Incorporación de Feriados

Se utilizó la librería `holidays` para generar un calendario oficial de Ecuador (`Ecuador()`) y detectar automáticamente los días feriados de cada año.

- Se añadió la variable binaria `es_feriado`, indicando si una fecha específica corresponde a un feriado nacional.
- Esta feature no depende del valor futuro del target, por lo que es segura para su uso en modelado supervisado.

---

## 🧠 Generación de Features Temporales Seguras

Con ayuda de `pytimetk`, se generaron múltiples características derivadas de la fecha que no requieren información futura, tales como:

- Día de la semana (`day_of_week`)
- Mes (`month`)
- Cuatrimestre (`quarter`)
- Número de semana (`week_of_year`)
- Día del mes (`day_of_month`)
- Indicadores adicionales:  
  - `is_weekend`, `is_month_start`, `is_month_end`

---

## 🛠️ Variables Derivadas Manuales

Se agregaron también variables diseñadas manualmente para capturar momentos clave del mes que pueden influir en el comportamiento de compra:

- `es_primer_dia_mes`
- `es_fin_de_mes`
- `es_mitad_de_mes` (rango 14–17)
- `dias_para_fin_mes`

Estas variables buscan capturar patrones asociados a fechas de pago, cierre de quincena o promociones específicas.

---

## 🔀 Interacciones de Variables Temporales

Se generaron interacciones relevantes para capturar efectos combinados entre contexto promocional y temporalidad:

- `promo × día de la semana`:  
  Captura sinergias entre campañas promocionales y comportamiento semanal.

- `feriado × día de la semana`:  
  Detección de si un feriado ocurre en día hábil o fin de semana, lo cual puede afectar la demanda.

---

In [15]:
###  Ingeniería de variables

def add_simple_date_position_features(df, date_col="date"):
    df = df.copy()
    date_series = pd.to_datetime(df[date_col])

    df["is_start_of_month"] = date_series.dt.day <= 3
    df["is_mid_month"] = date_series.dt.day.between(14, 17)
    df["is_end_of_month"] = date_series.dt.day >= (date_series.dt.days_in_month - 2)


    # df["day_category"] = np.select(
    #     [
    #         df["is_start_of_month"],
    #         df["is_mid_month"],
    #         df["is_end_of_month"]
    #     ],
    #     ["start", "mid", "end"],
    #     default="other"
    # )

    # Convertimos a int si lo requiere el modelo
    df["is_start_of_month"] = df["is_start_of_month"].astype(int)
    df["is_mid_month"] = df["is_mid_month"].astype(int)
    df["is_end_of_month"] = df["is_end_of_month"].astype(int)

    return df




hol_cal = HolCal(years=[2013,2017])

train_df['holy']=train_df['date'].isin(hol_cal).astype(int).values

test_df['holy']=test_df['date'].isin(hol_cal).astype(int).values

train_df2=train_df.merge(oil2, on="date",how="left").merge(stores,on="store_nbr",how="left")#.merge(holy[["date","type","transferred"]],on="date",how="left")
train_df2=train_df2.drop(["dcoilwtico","was_imputed"],axis=1)

test_df2=test_df.merge(oil2, on="date",how="left").merge(stores,on="store_nbr",how="left")#.merge(holy[["date","type","transferred"]],on="date",how="left")
test_df2=test_df2.drop(["dcoilwtico","was_imputed"],axis=1)



train_df2["hol"] = train_df2["date"].isin(holy["date"]).astype(int)
test_df2["hol"] = test_df2["date"].isin(holy["date"]).astype(int)

train_df2["recu"] = train_df2["date"].isin(holy.loc[holy["transferred"] == True, "date"]).astype(int)
test_df2["recu"] =test_df2["date"].isin(holy.loc[holy["transferred"] == True, "date"]).astype(int)


train_df2["imputed_value"]=train_df2["imputed_value"].interpolate()

test_df2["imputed_value"]=test_df2["imputed_value"].interpolate()

train_df2 = add_simple_date_position_features(train_df2)

test_df2=add_simple_date_position_features(test_df2)

train_df2.head()
# Counter(tidy['date'].isin(hol_cal).astype(int))

<frozen importlib._bootstrap>:1047: ImportWarning:

_PyDriveImportHook.find_spec() not found; falling back to find_module()

<frozen importlib._bootstrap>:1047: ImportWarning:

_BokehImportHook.find_spec() not found; falling back to find_module()

<frozen importlib._bootstrap>:1047: ImportWarning:

_PyDriveImportHook.find_spec() not found; falling back to find_module()

<frozen importlib._bootstrap>:1047: ImportWarning:

_BokehImportHook.find_spec() not found; falling back to find_module()

<frozen importlib._bootstrap>:1047: ImportWarning:

_PyDriveImportHook.find_spec() not found; falling back to find_module()

<frozen importlib._bootstrap>:1047: ImportWarning:

_BokehImportHook.find_spec() not found; falling back to find_module()



id       date  store_nbr      family  sales  onpromotion  holy  \
0   0 2013-01-01          1  AUTOMOTIVE    0.0            0     1   
1   1 2013-01-01          1   BABY CARE    0.0            0     1   
2   2 2013-01-01          1      BEAUTY    0.0            0     1   
3   3 2013-01-01          1   BEVERAGES    0.0            0     1   
4   4 2013-01-01          1       BOOKS    0.0            0     1   

   imputed_value   city      state type  cluster  hol  recu  \
0          93.14  Quito  Pichincha    D       13    1     0   
1          93.14  Quito  Pichincha    D       13    1     0   
2          93.14  Quito  Pichincha    D       13    1     0   
3          93.14  Quito  Pichincha    D       13    1     0   
4          93.14  Quito  Pichincha    D       13    1     0   

   is_start_of_month  is_mid_month  is_end_of_month  
0                  1             0                0  
1                  1             0                0  
2                  1             0                0  
3                  1             0                0  
4                  1             0                0

In [16]:
### cambio los nombres de date y la variable target porque es
### necesario en caso de usar prophet

train_df22=train_df2.copy().rename(columns={"date":"ds","sales":"y"})
test_df22=test_df2.copy().rename(columns={"date":"ds"})

In [17]:
from sklearn.preprocessing import PolynomialFeatures
from feature_engine.datetime import DatetimeFeatures
from feature_engine.creation import CyclicalFeatures
#  'month_start',
#  'month_end',
#  'quarter_start',
#  'quarter_end',
#  'year_start',
#  'year_end',
#  'leap_year',
#  'days_in_month',
#  'hour',
#  'minute',
#  'second'

def create_datetime_fourier_pipeline():
    """Crea pipeline para extraer features temporales y sus componentes cíclicos"""
    pipe1 = Pipeline(steps=[
        ("datetime_features", DatetimeFeatures(
            variables=["ds"],
            features_to_extract=[
                'month', 'quarter', 'semester', 'year', 'week',
                'day_of_week', 'day_of_month', 'day_of_year',
                'weekend', 'quarter_start'
            ],
            drop_original=False
        )),
        ('drop_constants', DropConstantFeatures(tol=0.975, missing_values='ignore')),
    ])
    return pipe1


def create_cyclical_pipeline(varfou):
    """Crea pipeline para aplicar codificación cíclica a features temporales"""
    return Pipeline(steps=[
        ("fourier", CyclicalFeatures(variables=varfou, drop_original=False)),
    ])


def create_cleaning_pipeline(var_all, cat_vars, discrete_vars, cont_vars, fechas):
    """Pipeline de limpieza, imputación, outliers, encoding y generación de interacciones"""
    return Pipeline([
        ('missing_indicator', AddMissingIndicator(variables=var_all)),
        ('frequent_imputation', CategoricalImputer(
            imputation_method='missing',
            variables=cat_vars + discrete_vars, ignore_format=True)),
        ('mean_imputation', MeanMedianImputer(
            imputation_method='median',
            variables=cont_vars)),
        ('out', Winsorizer(
            capping_method='gaussian',
            tail='right',
            fold=3,
            variables=cont_vars,
            add_indicators=True)),
        ('poly', SklearnTransformerWrapper(
            variables=['onpromotion', 'imputed_value', 'hol'] + fechas,
            transformer=PolynomialFeatures(degree=2, interaction_only=True, include_bias=False)
        )),
        ('ct', ce.TargetEncoder(
            cols=cat_vars + discrete_vars,
            min_samples_leaf=20,
            smoothing=10)),
        ('drop_features', DropConstantFeatures(tol=0.975, missing_values='ignore')),
    ])


def get_feature_importance(model, model_type='xgb'):
    """Extrae top N features importantes para XGBoost o LightGBM"""
    if model_type == 'xgb':
        importance_dict = model.get_booster().get_score(importance_type='gain')
        importance_df = pd.DataFrame({
            'feature': list(importance_dict.keys()),
            'gain': list(importance_dict.values())
        }).sort_values(by='gain', ascending=False)

    elif model_type == 'lgb':
        importance = model.booster_.feature_importance(importance_type='gain')
        feature_names = model.booster_.feature_name()
        importance_df = pd.DataFrame({
            'feature': feature_names,
            'gain': importance
        }).sort_values(by='gain', ascending=False)

    else:
        raise ValueError("model_type debe ser 'xgb' o 'lgb'")

    var_sel = importance_df['feature'].tolist()
    return importance_df, var_sel





<frozen importlib._bootstrap>:1047: ImportWarning:

_PyDriveImportHook.find_spec() not found; falling back to find_module()

<frozen importlib._bootstrap>:1047: ImportWarning:

_BokehImportHook.find_spec() not found; falling back to find_module()



## 📊 Preparación, Pipeline y Modelado Inicial

Para evitar **data leakage** y asegurar una evaluación correcta, se dividió el dataset en conjuntos de **train** y **test** antes de aplicar cualquier transformación.

---

### 🔄 Pipeline de Preprocesamiento

Se diseñó un pipeline completo con los siguientes pasos, aplicados exclusivamente al conjunto de entrenamiento para evitar fugas de información:

- **Indicadores de datos faltantes**  
  `AddMissingIndicator` sobre todas las variables relevantes (`var_all`).

- **Imputación para variables categóricas y discretas**  
  `CategoricalImputer` con método `'missing'` para las variables categóricas y discretas (`cat_vars + discrete_vars`).

- **Imputación para variables continuas**  
  `MeanMedianImputer` usando la mediana (`median`) para las variables continuas (`cont_vars`).

- **Tratamiento de valores extremos (Winsorización)**  
  `Winsorizer` con método gaussiano, límite en la cola derecha y fold=3, aplicado sobre variables continuas, añadiendo indicadores para valores capados.

- **Generación de interacciones polinómicas**  
  `PolynomialFeatures` de grado 2, con solo interacciones (sin términos cuadrados), aplicado a variables como `onpromotion`, `imputed_value`, `hol` y variables temporales (`var_t`).

- **Codificación Target Encoding para variables categóricas y discretas**  
  Utilizando `ce.TargetEncoder` con suavizado y mínimo de 20 muestras por hoja para evitar overfitting.

- **Eliminación de features constantes o casi constantes**  
  `DropConstantFeatures` con tolerancia 0.975 para eliminar variables con poca varianza.

---

### 🎯 Modelado Inicial con XGBoost

- Se entrenó un único modelo `XGBRegressor` sobre todo el conjunto de entrenamiento, considerando todas las combinaciones de `store_nbr` y `family`.
- Esta estrategia simplifica el entrenamiento y aprovecha patrones compartidos entre tiendas y familias.

---

### 🔍 Selección de Variables Importantes

- Tras el entrenamiento inicial, se seleccionaron las **41 variables más importantes** según la importancia calculada por XGBoost.
- Estas variables serán la base para la siguiente etapa de modelado **autoregresivo**, donde se incorporarán **lags** y **ventanas móviles**, aplicadas específicamente para cada combinación de `store_nbr` y `family`.

---

### 📈 Resultado Base y Próximos Pasos

- El modelo XGBoost inicial alcanzó un **SMAPE de 0.9** en la evaluación de Kaggle, estableciendo un baseline sólido para mejorar.
- El siguiente paso es construir modelos autoregresivos **por grupo (store_nbr + family)**, utilizando las variables seleccionadas y las nuevas características temporales y de lags, buscando superar este baseline.

---

> ⚠️ Este flujo garantiza que las transformaciones y selecciones se realicen sin filtración de información del test, manteniendo la validez y generalización del modelo.


In [18]:
def add_time_features(df, date_col='ds', periods=[1,2,6,7,13,14], max_order=2, engine="pandas"):
    df_dates = df[[date_col]].drop_duplicates()
    df_dates = df_dates.augment_fourier(
        date_column=date_col,
        periods=periods,
        max_order=max_order,
        engine=engine
    )
    df_dates = df_dates.augment_timeseries_signature(date_col)
    return df.merge(df_dates, on=date_col, how='left')
# --- SPLIT ---
target = ["y"]
X_train, X_test, y_train, y_test = train_test_split(
    train_df22.drop(target, axis=1),
    train_df22[target],
    test_size=0.2,
    random_state=0
)


df_trans = add_time_features(X_train)
df_trans2 = add_time_features(X_test)
df_trans_t = add_time_features(test_df22)

df_trans.head()

id         ds  store_nbr                      family  onpromotion  \
0  1757797 2015-09-16          3                  LADIESWEAR            0   
1   820517 2014-04-07         31                BREAD/BAKERY            0   
2  1464604 2015-04-04         52  SCHOOL AND OFFICE SUPPLIES            0   
3  1736105 2015-09-04         21                       DAIRY            3   
4   261037 2013-05-27         33                    CLEANING            0   

   holy  imputed_value           city                           state type  \
0     0      47.120000          Quito                       Pichincha    D   
1     0     100.430000       Babahoyo                        Los Rios    B   
2     0      50.439916          Manta                          Manabi    A   
3     0      46.020000  Santo Domingo  Santo Domingo de los Tsachilas    B   
4     0      93.840000        Quevedo                        Los Rios    C   

   ...  ds_mday  ds_qday  ds_yday  ds_weekend  ds_hour  ds_minute  ds_second  \
0  ...       16       78      259           0        0          0          0   
1  ...        7        7       97           0        0          0          0   
2  ...        4        4       94           0        0          0          0   
3  ...        4       66      247           0        0          0          0   
4  ...       27       57      147           0        0          0          0   

   ds_msecond  ds_nsecond  ds_am_pm  
0           0           0        am  
1           0           0        am  
2           0           0        am  
3           0           0        am  
4           0           0        am  

[5 rows x 69 columns]

In [19]:

var_t = df_trans.columns[df_trans.columns.str.\
                         contains(r"ds_(?!hour|minute|second|msecond|nsecond|am_pm)", regex=True)].tolist()


var_t = df_trans[var_t].select_dtypes(exclude="O").columns.tolist()

cat_vars,num_vars,discrete_vars,cont_vars,var_all=categ_vari(df_trans.drop(["id","ds"],axis=1))
pipe=Pipeline([
        ('missing_indicator', AddMissingIndicator(variables=var_all)),
        ('frequent_imputation', CategoricalImputer(
            imputation_method='missing',
            variables=cat_vars + discrete_vars, ignore_format=True)),
        ('mean_imputation', MeanMedianImputer(
            imputation_method='median',
            variables=cont_vars)),
        ('out', Winsorizer(
            capping_method='gaussian',
            tail='right',
            fold=3,
            variables=cont_vars,
            add_indicators=True)),
        ('poly', SklearnTransformerWrapper(
            variables=['onpromotion', 'imputed_value', 'hol'] + var_t,
            transformer=PolynomialFeatures(degree=2, interaction_only=True, include_bias=False)
        )),
        ('ct', ce.TargetEncoder(
            cols=cat_vars + discrete_vars,
            min_samples_leaf=20,
            smoothing=10)),
        ('drop_features', DropConstantFeatures(tol=0.975, missing_values='ignore')),
    ])

X_train2 = pipe.fit_transform(df_trans, y_train.reset_index(drop=True))
X_test2 = pipe.transform(df_trans2)
test_df3 = pipe.transform(df_trans_t)

X_train2.head()

id         ds  store_nbr       family        city       state  \
0  1757797 2015-09-16          3     7.151777  557.162706  554.851553   
1   820517 2014-04-07         31   463.580744  318.604182  286.821518   
2  1464604 2015-04-04         52     2.927411  125.097751  149.577310   
3  1736105 2015-09-04         21   708.404978  215.496647  215.496647   
4   261037 2013-05-27         33  1070.983309  255.230668  286.821518   

         type     cluster  is_start_of_month  is_mid_month  ...  \
0  351.170770  651.594593         352.757526    350.726098  ...   
1  327.770870  255.911887         352.757526    359.295059  ...   
2  705.932244  604.893948         352.757526    359.295059  ...   
3  327.770870  344.357887         352.757526    359.295059  ...   
4  197.677750  194.793606         352.757526    359.295059  ...   

   ds_wday ds_mday  ds_wday ds_qday  ds_wday ds_yday  ds_wday ds_weekend  \
0             48.0            234.0            777.0                 0.0   
1              7.0              7.0             97.0                 0.0   
2             24.0             24.0            564.0                 0.0   
3             20.0            330.0           1235.0                 0.0   
4             27.0             57.0            147.0                 0.0   

   ds_mday ds_qday  ds_mday ds_yday  ds_mday ds_weekend  ds_qday ds_yday  \
0           1248.0           4144.0                 0.0          20202.0   
1             49.0            679.0                 0.0            679.0   
2             16.0            376.0                 0.0            376.0   
3            264.0            988.0                 0.0          16302.0   
4           1539.0           3969.0                 0.0           8379.0   

   ds_qday ds_weekend  ds_yday ds_weekend  
0                 0.0                 0.0  
1                 0.0                 0.0  
2                 0.0                 0.0  
3                 0.0                 0.0  
4                 0.0                 0.0  

[5 rows x 950 columns]

In [ ]:
import time
# --- MODELO ---
tt = time.time()

model_type = 'xgb'
model = XGBRegressor(random_state=42)
# model_type = 'lgb'
# model = lgb.LGBMRegressor(random_state=42)

model.fit(X_train2.drop(["id", "ds"], axis=1), y_train)
# --- PREDICCIÓN Y MÉTRICAS ---
y_pred = model.predict(X_test2.drop(["id", "ds"], axis=1))
print("R²:", r2_score(y_test, y_pred))

elap = time.time() - tt
print(f"Tiempo de ejecución: {elap:.2f} segundos")

R²: 0.94288170337677
Tiempo de ejecución: 492.13 segundos


In [ ]:
# --- IMPORTANCIA DE FEATURES ---
importance_df, var_sel = get_feature_importance(model, model_type=model_type)
var_sel=var_sel[:41]
# --- OUTPUT DE FEATURES IMPORTANTES ---
display(importance_df.head(20),var_sel)

feature          gain
0                            family  2.032094e+09
6               onpromotion ds_half  1.180029e+09
1                           cluster  1.167413e+09
3                    ds_quarteryear  7.933663e+08
2               onpromotion ds_wday  7.922995e+08
4              ds_index_num ds_wday  6.582651e+08
5          onpromotion ds_index_num  5.024544e+08
7                         store_nbr  4.532258e+08
8                       ds_wday_lbl  4.294867e+08
9               ds_year_iso ds_wday  3.699421e+08
11        is_start_of_month ds_yday  3.180603e+08
12                             city  2.278544e+08
10  imputed_value is_start_of_month  2.037997e+08
13                     ds_month_lbl  2.024191e+08
14          onpromotion ds_year_iso  1.996939e+08
22               ds_quarter ds_qday  1.696691e+08
17             onpromotion ds_month  1.605485e+08
21     is_start_of_month ds_sin_2_7  1.469624e+08
19            imputed_value ds_wday  1.464144e+08
20                 ds_yweek ds_yday  1.435867e+08

['family',
 'onpromotion ds_half',
 'cluster',
 'ds_quarteryear',
 'onpromotion ds_wday',
 'ds_index_num ds_wday',
 'onpromotion ds_index_num',
 'store_nbr',
 'ds_wday_lbl',
 'ds_year_iso ds_wday',
 'is_start_of_month ds_yday',
 'city',
 'imputed_value is_start_of_month',
 'ds_month_lbl',
 'onpromotion ds_year_iso',
 'ds_quarter ds_qday',
 'onpromotion ds_month',
 'is_start_of_month ds_sin_2_7',
 'imputed_value ds_wday',
 'ds_yweek ds_yday',
 'ds_year ds_month',
 'ds_wday ds_mday',
 'hol ds_sin_1_14',
 'ds_year ds_mday',
 'hol ds_yweek',
 'ds_year ds_yday',
 'ds_mweek',
 'ds_index_num ds_mday',
 'ds_yweek ds_qday',
 'ds_leapyear ds_yweek',
 'imputed_value ds_year',
 'is_start_of_month ds_sin_2_13',
 'ds_index_num ds_half',
 'ds_sin_1_2 ds_weekend',
 'ds_month ds_mday',
 'ds_index_num ds_weekend',
 'imputed_value ds_mday',
 'ds_index_num ds_month',
 'ds_half ds_yweek',
 'ds_cos_1_13 ds_mday',
 'ds_month ds_qday']

In [ ]:
tt = time.time()
model.fit(X_train2.drop(["id", "ds"], axis=1)[var_sel], y_train)


# --- PREDICCIÓN Y MÉTRICAS ---
y_pred = model.predict(X_test2.drop(["id", "ds"], axis=1)[var_sel])
print("R²:", r2_score(y_test, y_pred))

elap = time.time() - tt
print(f"Tiempo de ejecución: {elap:.2f} segundos")

R²: 0.9434276223182678
Tiempo de ejecución: 20.88 segundos


In [ ]:

cat_vars,num_vars,discrete_vars,cont_vars,var_all=categ_vari(df_trans.drop(["id","ds","store_nbr","family"],axis=1))
pipe=Pipeline([
        ('missing_indicator', AddMissingIndicator(variables=var_all)),
        ('frequent_imputation', CategoricalImputer(
            imputation_method='missing',
            variables=cat_vars + discrete_vars, ignore_format=True)),
        ('mean_imputation', MeanMedianImputer(
            imputation_method='median',
            variables=cont_vars)),
        ('out', Winsorizer(
            capping_method='gaussian',
            tail='right',
            fold=3,
            variables=cont_vars,
            add_indicators=True)),
        ('poly', SklearnTransformerWrapper(
            variables=['onpromotion', 'imputed_value', 'hol'] + var_t,
            transformer=PolynomialFeatures(degree=2, interaction_only=True, include_bias=False)
        )),
        ('ct', ce.TargetEncoder(
            cols=cat_vars + discrete_vars,
            min_samples_leaf=20,
            smoothing=10)),
        ('drop_features', DropConstantFeatures(tol=0.975, missing_values='ignore')),
    ])

X_train2 = pipe.fit_transform(df_trans, y_train.reset_index(drop=True))
X_test2 = pipe.transform(df_trans2)
test_df3 = pipe.transform(df_trans_t)

X_train2.head()

id         ds  store_nbr                      family        city  \
0  1757797 2015-09-16          3                  LADIESWEAR  557.162706   
1   820517 2014-04-07         31                BREAD/BAKERY  318.604182   
2  1464604 2015-04-04         52  SCHOOL AND OFFICE SUPPLIES  125.097751   
3  1736105 2015-09-04         21                       DAIRY  215.496647   
4   261037 2013-05-27         33                    CLEANING  255.230668   

        state        type     cluster  ds_quarteryear  ds_month_lbl  ...  \
0  554.851553  351.170770  651.594593      418.453330    365.134171  ...   
1  286.821518  327.770870  255.911887      243.769027    340.379757  ...   
2  149.577310  705.932244  604.893948      335.919453    340.379757  ...   
3  215.496647  327.770870  344.357887      418.453330    365.134171  ...   
4  286.821518  197.677750  194.793606      211.609955    342.514977  ...   

   ds_wday ds_mday  ds_wday ds_qday  ds_wday ds_yday  ds_wday ds_weekend  \
0             48.0            234.0            777.0                 0.0   
1              7.0              7.0             97.0                 0.0   
2             24.0             24.0            564.0                 0.0   
3             20.0            330.0           1235.0                 0.0   
4             27.0             57.0            147.0                 0.0   

   ds_mday ds_qday  ds_mday ds_yday  ds_mday ds_weekend  ds_qday ds_yday  \
0           1248.0           4144.0                 0.0          20202.0   
1             49.0            679.0                 0.0            679.0   
2             16.0            376.0                 0.0            376.0   
3            264.0            988.0                 0.0          16302.0   
4           1539.0           3969.0                 0.0           8379.0   

   ds_qday ds_weekend  ds_yday ds_weekend  
0                 0.0                 0.0  
1                 0.0                 0.0  
2                 0.0                 0.0  
3                 0.0                 0.0  
4                 0.0                 0.0  

[5 rows x 1065 columns]

In [23]:
var_sel=['onpromotion ds_year_iso',
 'ds_month ds_yweek',
 'onpromotion ds_half',
 'family',
 'onpromotion ds_wday',
 'ds_year_iso ds_wday',
 'cluster',
 'onpromotion ds_index_num',
 'ds_half ds_yweek',
 'onpromotion ds_month',
 'ds_index_num ds_wday',
 'ds_quarteryear',
 'ds_sin_1_7 ds_leapyear',
 'ds_year ds_mday',
 'ds_year ds_month',
 'ds_mday',
 'hol ds_sin_1_14',
 'store_nbr',
 'ds_sin_1_2 ds_cos_1_14',
 'ds_wday_lbl',
 'hol ds_cos_1_6',
 'hol ds_sin_2_7',
 'imputed_value ds_wday',
 'ds_cos_1_1 ds_month',
 'ds_quarter ds_qday',
 'city',
 'ds_yday',
 'onpromotion ds_year',
 'onpromotion',
 'ds_wday ds_mday',
 'ds_leapyear ds_qday',
 'hol ds_yweek',
 'ds_sin_1_1 ds_mday',
 'onpromotion ds_sin_1_7',
 'imputed_value ds_mday',
 'ds_sin_1_6 ds_cos_1_2',
 'onpromotion ds_sin_1_1',
 'ds_index_num ds_mday',
 'ds_month_lbl',
 'hol ds_sin_2_13',
 'imputed_value ds_month']

In [24]:

df_tr=pd.concat([X_train2,X_test2])
y_tr=pd.concat([y_train,y_test])

y_tr.index=df_tr.index
df_tr=pd.concat([df_tr,y_tr],axis=1)[["ds","y"]+var_sel]
df_tt2=test_df3[["ds"]+var_sel]

In [25]:
df_tr.head()

ds      y  onpromotion ds_year_iso  ds_month ds_yweek  \
0 2015-09-16   27.0                      0.0              342.0   
1 2014-04-07  382.0                      0.0               60.0   
2 2015-04-04    0.0                      0.0               56.0   
3 2015-09-04  373.0                   6045.0              324.0   
4 2013-05-27  880.0                      0.0              110.0   

   onpromotion ds_half       family  onpromotion ds_wday  ds_year_iso ds_wday  \
0                  0.0     7.151777                  0.0               6045.0   
1                  0.0   463.580744                  0.0               2014.0   
2                  0.0     2.927411                  0.0              12090.0   
3                  6.0   708.404978                 15.0              10075.0   
4                  0.0  1070.983309                  0.0               2013.0   

      cluster  onpromotion ds_index_num  ...  hol ds_yweek  \
0  651.594593              0.000000e+00  ...           0.0   
1  255.911887              0.000000e+00  ...           0.0   
2  604.893948              0.000000e+00  ...           0.0   
3  344.357887              4.323974e+09  ...           0.0   
4  194.793606              0.000000e+00  ...           0.0   

   ds_sin_1_1 ds_mday  onpromotion ds_sin_1_7  imputed_value ds_mday  \
0          -15.567640               -0.000000             753.920000   
1           -2.097200               -0.000000             703.010000   
2            1.507666               -0.000000             201.759663   
3            2.571710                1.025987             184.080000   
4           22.325944                0.000000            2533.680000   

   ds_sin_1_6 ds_cos_1_2  onpromotion ds_sin_1_1  ds_index_num ds_mday  \
0              -0.575848               -0.000000          2.307779e+10   
1               0.151356               -0.000000          9.777802e+09   
2               0.816561                0.000000          5.712422e+09   
3               0.135492                1.928783          5.765299e+09   
4               0.296261                0.000000          3.697955e+10   

   ds_month_lbl  hol ds_sin_2_13  imputed_value ds_month  
0    365.134171              0.0              424.080000  
1    340.379757             -0.0              401.720000  
2    340.379757             -0.0              201.759663  
3    365.134171              0.0              414.180000  
4    342.514977              0.0              469.200000  

[5 rows x 43 columns]

## 🔁 Modelo Autoregresivo por Grupo (`store_nbr` y `family`)

Se implementó un enfoque **autoregresivo individualizado**, entrenando un modelo por cada combinación única de **tienda (`store_nbr`)** y **familia de productos (`family`)**.

Este enfoque permite capturar dinámicas específicas de venta en cada contexto local, utilizando:

- Las **41 variables más importantes** seleccionadas previamente con SHAP.
- **Lags informativos**: `lag_1`, `lag_2`, `lag_6`, `lag_7`, `lag_13`, `lag_14`.
- **Ventanas móviles**: `rolling_mean_14`, `rolling_std_14`, entre otras.
- Variables temporales e interacciones clave con promociones y fechas del calendario (inicio, mitad y fin de mes).

Se recomienda **validar primero el modelo para un solo grupo**, comprobando:
  - Calidad del ajuste.
  - Estabilidad temporal.
  - Impacto real de los lags y variables temporales.
  - Establecer un modelo de stacking por grupo.

---

### ⚙️ Después debemos paralelizar

Para mejorar el rendimiento computacional y permitir escalabilidad:

- Una vez verificado el pipeline, se procederá a **paralelizar el entrenamiento** usando `Parallel` de `joblib`, lo cual permitirá:
  - Distribuir el cómputo por núcleos.
  - Reducir los tiempos de entrenamiento significativamente.

---

> 🧠 Este enfoque permitió alcanzar un **SMAPE de 0.43318 en Kaggle**, y constituye la base para futuras mejoras como el **ajuste hiperparamétrico fino por estimador**.


In [20]:
from tqdm import tqdm
import time
from sklearn.ensemble import StackingRegressor
from sklearn.linear_model import RidgeCV
from feature_engine.timeseries.forecasting import LagFeatures,WindowFeatures, ExpandingWindowFeatures
tt = time.time()

def run_recursive_forecast_by_group2(train_df2, test_df2, model, y_col="y"):
    all_preds = []

    # Detectar nombre de la columna de fecha si no es 'date'
    date_col = [col for col in train_df2.columns if col.lower() in ["date", "ds"]][0]

    grouped = train_df2.groupby(['store_nbr', 'family']).count().index.tolist()

    for s, f in tqdm(grouped):
        # Filtrado por grupo
        df_hist = train_df2[(train_df2.store_nbr == s) & (train_df2.family == f)].copy().set_index(date_col)
        df_test = test_df2[(test_df2.store_nbr == s) & (test_df2.family == f)].copy().set_index(date_col)

        # Variables exógenas
        exo2 = [var for var in df_test.columns if var != y_col]

        # Fechas
        forecast_horizon = df_test.index
        forecast_start_time = forecast_horizon.min()
        look_back_window_size = pd.DateOffset(days=14)
        look_back_start_time = forecast_start_time - look_back_window_size

        # --- CREAR df_predict extendido ---
        df_predict = df_hist[[y_col]].loc[look_back_start_time:].copy()
        df_exo = pd.concat([
            df_hist[exo2].loc[look_back_start_time:],
            df_test[exo2]
        ], axis=0)

        df_predict = pd.concat([df_predict, pd.DataFrame(index=forecast_horizon)])
        df_predict = pd.concat([df_predict, df_exo], axis=1).sort_index()

        # --- PIPELINE DE FEATURES HISTÓRICOS ---
        fe_pipeline2 = Pipeline([
            ("lags", LagFeatures(variables=[y_col], periods=[1,2,6,7,9,13,14], missing_values='ignore')),
            ("windows", WindowFeatures(variables=[y_col], window=[14], functions=['mean', "max", 'std'], missing_values='ignore')),
            ("windows2", ExpandingWindowFeatures(
            variables=[y_col],
            periods=14,
            functions=['mean', "max", 'std'],
            missing_values='ignore'))
        ])

        df_hist_reset = df_hist.copy().reset_index()
        df_hist_reset = fe_pipeline2.fit_transform(df_hist_reset).set_index(date_col)

        # --- ENTRENAR MODELO ---
        X0 = df_hist_reset.drop(columns=[y_col], axis=1)
        y0 = df_hist_reset[y_col]

        # cat_vars, num_vars, discrete_vars, cont_vars, var_all = categ_vari(X0.drop("id", axis=1))
        cat_vars, num_vars, discrete_vars, cont_vars, var_all = categ_vari(X0)
        pipe1 = Pipeline([
            ('missing_indicator', AddMissingIndicator(variables=var_all)),
            ('frequent_imputation', CategoricalImputer(imputation_method='missing', variables=cat_vars + discrete_vars, ignore_format=True)),
            ('mean_imputation', MeanMedianImputer(imputation_method='median', variables=cont_vars)),
            ('out', Winsorizer(capping_method='gaussian', tail='right', fold=3, variables=cont_vars, add_indicators=True)),
            ('rare_label_encoder', RareLabelEncoder(tol=0.01, n_categories=1, variables=cat_vars + discrete_vars, ignore_format=True)),
            ('ct', ce.TargetEncoder(cols=cat_vars + discrete_vars, min_samples_leaf=20, smoothing=10)),
            ('drop_features', DropConstantFeatures(tol=0.975, missing_values='ignore')),
        ])

        X0 = pipe1.fit_transform(X0, y0)

        xgb_model = XGBRegressor(random_state=42)
        lgb_model = lgb.LGBMRegressor(random_state=42)
        # Meta-modelo
        meta_model = RidgeCV()

        # Stacking
        stack = StackingRegressor(
            estimators=[
                ('xgb', xgb_model),
                ('lgb', lgb_model)
            ],
            final_estimator=meta_model,
            cv=2,
            # passthrough=True  # Opcional: pasar features originales al meta-modelo
)

        # model.fit(X0, y0)
        stack.fit(X0, y0)

        # --- PREDICCIÓN RECURSIVA ---
        preds = []
        for step_date in forecast_horizon:
            df_temp = df_predict.loc[:step_date].copy()

            df_features = df_temp.reset_index()
            df_features = fe_pipeline2.transform(df_features).set_index(date_col)

            X_step = df_features.drop(columns=[y_col], axis=1)
            X_step = pipe1.transform(X_step)

            # y_pred = model.predict(X_step)

            y_pred = stack.predict(X_step)
            y_pred = pd.DataFrame(y_pred, index=X_step.index, columns=[y_col])
            y_pred = pd.concat([X_step, y_pred], axis=1)

            y_pred = y_pred.loc[step_date, y_col]
            preds.append(y_pred)
            df_predict.loc[step_date, y_col] = y_pred

        df_result = df_test.copy()
        df_result["prediction"] = preds
        all_preds.append(df_result.reset_index())

        elap = time.time()
        print(s, f, elap - tt)
        break

    return pd.concat(all_preds)


In [26]:
final_preds = run_recursive_forecast_by_group2(df_tr, df_tt2, XGBRegressor(random_state=42))
final_preds

  0%|          | 0/1782 [00:00<?, ?it/s]

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000567 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 4456
[LightGBM] [Info] Number of data points in the train set: 1684, number of used features: 47
[LightGBM] [Info] Start training from score 0.125297
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive g

  0%|          | 0/1782 [00:03<?, ?it/s]

1 0.06972754100610802 67.92748522758484


ds  onpromotion ds_year_iso  ds_month ds_yweek  \
0  2017-08-16                      0.0              264.0   
1  2017-08-17                      0.0              264.0   
2  2017-08-18                      0.0              264.0   
3  2017-08-19                      0.0              264.0   
4  2017-08-20                      0.0              264.0   
5  2017-08-21                      0.0              272.0   
6  2017-08-22                      0.0              272.0   
7  2017-08-23                      0.0              272.0   
8  2017-08-24                      0.0              272.0   
9  2017-08-25                      0.0              272.0   
10 2017-08-26                      0.0              272.0   
11 2017-08-27                      0.0              272.0   
12 2017-08-28                      0.0              280.0   
13 2017-08-29                      0.0              280.0   
14 2017-08-30                      0.0              280.0   
15 2017-08-31                      0.0              280.0   

    onpromotion ds_half    family  onpromotion ds_wday  ds_year_iso ds_wday  \
0                   0.0  0.069728                  0.0               6051.0   
1                   0.0  0.069728                  0.0               8068.0   
2                   0.0  0.069728                  0.0              10085.0   
3                   0.0  0.069728                  0.0              12102.0   
4                   0.0  0.069728                  0.0              14119.0   
5                   0.0  0.069728                  0.0               2017.0   
6                   0.0  0.069728                  0.0               4034.0   
7                   0.0  0.069728                  0.0               6051.0   
8                   0.0  0.069728                  0.0               8068.0   
9                   0.0  0.069728                  0.0              10085.0   
10                  0.0  0.069728                  0.0              12102.0   
11                  0.0  0.069728                  0.0              14119.0   
12                  0.0  0.069728                  0.0               2017.0   
13                  0.0  0.069728                  0.0               4034.0   
14                  0.0  0.069728                  0.0               6051.0   
15                  0.0  0.069728                  0.0               8068.0   

       cluster  onpromotion ds_index_num  ds_half ds_yweek  ...  \
0   323.742773                       0.0              66.0  ...   
1   323.742773                       0.0              66.0  ...   
2   323.742773                       0.0              66.0  ...   
3   323.742773                       0.0              66.0  ...   
4   323.742773                       0.0              66.0  ...   
5   323.742773                       0.0              68.0  ...   
6   323.742773                       0.0              68.0  ...   
7   323.742773                       0.0              68.0  ...   
8   323.742773                       0.0              68.0  ...   
9   323.742773                       0.0              68.0  ...   
10  323.742773                       0.0              68.0  ...   
11  323.742773                       0.0              68.0  ...   
12  323.742773                       0.0              70.0  ...   
13  323.742773                       0.0              70.0  ...   
14  323.742773                       0.0              70.0  ...   
15  323.742773                       0.0              70.0  ...   

    ds_sin_1_1 ds_mday  onpromotion ds_sin_1_7  imputed_value ds_mday  \
0             0.000000                     0.0             748.800000   
1            16.631790                    -0.0             800.190000   
2            -7.290659                    -0.0             874.620000   
3           -15.402425                    -0.0             923.178022   
4            14.813006                    -0.0             959.769705   
5            10.584461                     0.0     

In [27]:

### Se paraleliza el flujo de trabajo
from joblib import Parallel, delayed
from tqdm import tqdm
import time
from sklearn.pipeline import Pipeline
from feature_engine.timeseries.forecasting import LagFeatures, WindowFeatures, ExpandingWindowFeatures

def forecast_one_group_feat(s, f, train_df2, test_df2, model, y_col, date_col):
    # Copiar modelo para evitar side effects en paralelo
    import copy
    model = copy.deepcopy(model)

    df_hist = train_df2[(train_df2.store_nbr == s) & (train_df2.family == f)].copy().set_index(date_col)
    df_test = test_df2[(test_df2.store_nbr == s) & (test_df2.family == f)].copy().set_index(date_col)

    exo2 = [var for var in df_test.columns if var != y_col]
    forecast_horizon = df_test.index
    forecast_start_time = forecast_horizon.min()
    look_back_start_time = forecast_start_time - pd.DateOffset(days=14)

    df_predict = df_hist[[y_col]].loc[look_back_start_time:].copy()
    df_exo = pd.concat([
        df_hist[exo2].loc[look_back_start_time:],
        df_test[exo2]
    ], axis=0)

    df_predict = pd.concat([df_predict, pd.DataFrame(index=forecast_horizon)])
    df_predict = pd.concat([df_predict, df_exo], axis=1).sort_index()

    fe_pipeline2 = Pipeline([
        ("lags", LagFeatures(variables=[y_col], periods=[1,2,6,7,9,13,14], missing_values='ignore')),
        ("windows", WindowFeatures(variables=[y_col], window=[14], functions=['mean', "max", 'std'], missing_values='ignore')),
        ("windows2", ExpandingWindowFeatures(variables=[y_col], periods=14, functions=['mean', "max", 'std'], missing_values='ignore'))
    ])

    df_hist_reset = df_hist.copy().reset_index()
    df_hist_reset = fe_pipeline2.fit_transform(df_hist_reset).set_index(date_col)

    X0 = df_hist_reset.drop(columns=[y_col], axis=1)
    y0 = df_hist_reset[y_col]

    cat_vars, num_vars, discrete_vars, cont_vars, var_all = categ_vari(X0)

    pipe1 = Pipeline([
        ('missing_indicator', AddMissingIndicator(variables=var_all)),
        ('frequent_imputation', CategoricalImputer(imputation_method='missing', variables=cat_vars + discrete_vars, ignore_format=True)),
        ('mean_imputation', MeanMedianImputer(imputation_method='median', variables=cont_vars)),
        ('out', Winsorizer(capping_method='gaussian', tail='right', fold=3, variables=cont_vars, add_indicators=True)),
        ('rare_label_encoder', RareLabelEncoder(tol=0.01, n_categories=1, variables=cat_vars + discrete_vars, ignore_format=True)),
        ('ct', ce.TargetEncoder(cols=cat_vars + discrete_vars, min_samples_leaf=20, smoothing=10)),
        ('drop_features', DropConstantFeatures(tol=0.975, missing_values='ignore')),
    ])

    X0 = pipe1.fit_transform(X0, y0)
    xgb_model = XGBRegressor(random_state=42)
    lgb_model = lgb.LGBMRegressor(random_state=42)
    # Meta-modelo
    meta_model = RidgeCV()

    # Stacking
    stack = StackingRegressor(
        estimators=[
            ('xgb', xgb_model),
            ('lgb', lgb_model)
        ],
        final_estimator=meta_model,
        cv=2,
        # passthrough=True  # Opcional: pasar features originales al meta-modelo
            )
    # model.fit(X0, y0)
    stack.fit(X0, y0)
    preds = []
    for step_date in forecast_horizon:
        df_temp = df_predict.loc[:step_date].copy()
        df_features = df_temp.reset_index()
        df_features = fe_pipeline2.transform(df_features).set_index(date_col)

        X_step = df_features.drop(columns=[y_col], axis=1)
        X_step = pipe1.transform(X_step)

        # y_pred = model.predict(X_step)
        y_pred = stack.predict(X_step)
        y_pred = pd.DataFrame(y_pred, index=X_step.index, columns=[y_col])
        y_pred = y_pred.loc[step_date, y_col]
        preds.append(y_pred)
        df_predict.loc[step_date, y_col] = y_pred

    df_result = df_test.copy()
    df_result["prediction"] = preds
    return df_result.reset_index()


def run_recursive_forecast_by_group2(train_df2, test_df2, model, y_col="y", n_jobs=-1):
    date_col = [col for col in train_df2.columns if col.lower() in ["date", "ds"]][0]
    grouped = train_df2.groupby(['store_nbr', 'family']).count().index.tolist()

    print(f"⏱️ Starting parallel forecast over {len(grouped)} groups")
    t0 = time.time()
    results = Parallel(n_jobs=n_jobs)(
        delayed(forecast_one_group_feat)(s, f, train_df2, test_df2, model, y_col, date_col)
        for s, f in tqdm(grouped)
    )
    print(f"✅ Done in {time.time() - t0:.2f}s")

    return pd.concat(results)


In [ ]:
df_preds = run_recursive_forecast_by_group2(df_tr, df_tt2, model=XGBRegressor(random_state=42), y_col="y", n_jobs=-1)

df_preds

⏱️ Starting parallel forecast over 1782 groups


  0%|          | 0/1782 [00:00<?, ?it/s]<frozen importlib._bootstrap>:1047: ImportWarning:

_PyDriveImportHook.find_spec() not found; falling back to find_module()

<frozen importlib._bootstrap>:1047: ImportWarning:

_BokehImportHook.find_spec() not found; falling back to find_module()

 54%|█████▎    | 956/1782 [25:15<22:19,  1.62s/it]

In [ ]:

### Exporto los resultados para Kaggle
### de acuerdo al formato proveído en 'submission.csv'
df_results=df_preds[["ds","store_nbr","family","prediction"]]


df_results.columns=["date","store_nbr","family","sales"]


df_results["sales"]=np.where(
df_results["sales"]<0,0,
df_results["sales"])
final=test_df2[["id","store_nbr","family","date"]].merge(df_results,on=["store_nbr","family","date"],how="left")[["id","sales"]]

final.to_csv("final.csv",index=False)
files.download("final.csv")


### 📊 Resultados

- En la evaluación final de Kaggle, este enfoque alcanzó un **SMAPE de 0.43318**, lo que representa un rendimiento sólido y competitivo dentro de la competencia.
- Este resultado mejora significativamente el baseline inicial (SMAPE 0.9) logrado con el modelo global XGBoost, demostrando la efectividad del modelado específico por grupo.

---

### 🔮 Próximos Pasos: Nuevas Features


- Se puede explorar la inclusión de indicadores económicos o sociales adicionales, como la proximidad a fechas de pago específicas o datos macroeconómicos de consumo regional.Sin embargo, se mantiene un enfoque pragmático para evitar agregar variables irrelevantes o ruido que compliquen el modelo.

---



## 📝 Conclusiones

- Esta metodología de modelado específico por grupo ha mostrado un buen rendimiento en un conjunto de datos grande (~3 millones de filas), lo cual es significativo dada la complejidad y heterogeneidad de las series temporales.
- Para optimizar el entrenamiento, se recomienda utilizar **paralelización (Parallel processing)** en el modelo autoregresivo, dado el volumen y cantidad de submodelos individuales.
- El modelo autoregresivo superó en rendimiento a enfoques populares como **Skforecast** y **Prophet**, aunque para mantener la concisión del reporte no se incluyen todos los detalles comparativos.
- El pipeline y la selección cuidadosa de features, combinadas con el análisis de lags y estacionalidad, fueron clave para obtener esta mejora.
- Entre posibles desafíos están la gestión del sesgo en la imputación y la necesidad de mantener el control de la complejidad para evitar sobreajuste.
- En general, el balance entre rigor técnico y pragmatismo en el diseño permitió construir un modelo robusto, escalable y con potencial para seguir mejorando en iteraciones futuras.

---
### ⚙️ Importancia del Entorno de Ejecución (Google Colab)

- Todo el proceso fue desarrollado y ejecutado en **Google Colab**, utilizando recursos avanzados como **TPU runtime** y **hasta 60 GB de RAM**.
- La ejecución intensiva de tareas como **selección de variables, ingeniería de interacciones y evaluación cruzada** hizo uso completo de esa capacidad.
- Dado que las sesiones de Colab tienen un límite de uso intensivo de **~2 horas** antes de reiniciarse automáticamente, fue **crucial realizar una cuidadosa selección de features** para reducir el tiempo de entrenamiento por iteración.
- Este entorno permitió manejar un dataset de más de **3 millones de filas**, algo inviable en entornos de bajo recurso.

---

### 🚀 Lecciones y Aportes

- El uso de **pipelines modulares**, **interacciones automáticas** y la separación estricta entre entrenamiento y validación permitió mantener un flujo reproducible, escalable y seguro ante fugas de información.
- Se destacó la **eficacia del modelado por grupo**, que superó alternativas como Prophet y Skforecast.
- Aunque no se reportan todos los experimentos por limitaciones de espacio, se priorizó lo más relevante para explicar el rendimiento alcanzado.

---
> 💡 En resumen, esta solución representa un enfoque sólido y escalable para problemas de predicción de ventas en grandes catálogos con múltiples tiendas y familias, integrando técnicas avanzadas de feature engineering y modelado temporal.
